# Projet FDD - Arthur Brandao & Maxence Bacquet

L'objectif du projet est récupérer la liste des anime regardés par un utilisateur sur le site Anilist.co pour lui faire des recommendations.

## Import

Import des class utile pour la recommendation. La class AnilistApi et AnilistQuery ont été créées à l'occasion de ce projet pour permettre d'interroger facielement l'API. de plus l'API d'Anilist utilisant GraphQL une class GraphQLClient à aussi été créée pour l'occasion et est utiliser par la class AnilistApi.

In [1]:
import numpy as np
import pandas as pd
from anilist_api import AnilistApi
from anilist_api import AnilistQuery
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
# Affichage des versions
print('numpy: {}'.format(np.__version__))
print('pandas: {}'.format(pd.__version__))

numpy: 1.16.4
pandas: 0.25.2


Définition des variable utile pour tous le projet (variable global et instance d'objet)

In [2]:
# Le nom de l'utilisateur pour qui sont faite les recommendations
USER = 'Loquicom'
# La precision minimum du model lors de la phase de test (en %) /!\ Un trop grand nombre peut être impossible à atteindre
ACCURACYMIN = 80
# Nombre d'iteration maximum avant de considerer que le model ne peut pas atteindre la précision démandée (pourr éviter une boucle infini)
ITERATIONMAX = 25 # -1 <=> Pas de limite
# Le nombre de requete effectué pour la recherche
NBITERATION = 4
# Le nombre d'anime récupérés par requete (max 50)
NBANIME = 50
# L'api d'Anilist
anilist = AnilistApi()
# Le modèle utilisé pour l'apprentissage des features utile à la recommendation
model = RandomForestClassifier(n_estimators = 1000, random_state = 42, max_features=10)

## Definition des fonctions utilitaires

  - **valid_data**: Permet de verifier et mesurer la precision des données predite par le model
  - **identical_features**: Fait en sorte que le dataframe est les même feature que la dataframe source
  - **make_querry**: Création d'une query basique utile pour requeter l'api d'Anilist

In [3]:
def valid_data(predict, value):
    result = pd.Series(value - predict)
    error = result[result != 0].count()
    accuracy = 100 - ((error / result.size) * 100)
    return result.size, error, accuracy

def identical_features(source, target, keep = []):
    if keep is str:
        keep = [keep]
    # Ajout feature manquante
    for feature in source.columns:
        if feature not in target.columns:
            target[feature] = 0
    # Suppr feature en trop
    drop = []
    for feature in target.columns:
        if feature not in source.columns and feature not in keep:
            drop.append(feature)
    return target.drop(drop, axis = 1)

def make_query(score = -1, popularity = -1, epMin = -1, epMax = -1, durationMin = -1, durationMax = -1, source = [], formatType = []):
    query = AnilistQuery()
    if score != -1:
        query.scoreGreaterThan(score)
    if popularity != -1:
        query.popularityGreaterThan(popularity)
    if epMin != -1:
        query.episodeBetween(epMin, epMax)
    if durationMin != -1:
        query.durationBetween(durationMin, durationMax)
    if len(formatType) > 0:
        query.formatIn(formatType)
    if len(source) > 0:
        query.sourceIn(source)
    return query

## Récupèration des données

Les données sont récupérées sur l'API d'Anilist. Les données utilisées correspondent à la liste des anime complétés par l'utilisateur. Dans les données on retrouve notamment le score donné par l'utilisateur, le score moyen sur le site, le nombre d'episode et leur durée, la popularité, des tags, les genre, le format et la source.

In [4]:
animelist = anilist.findUser(USER).getUserAnimeList()
completedList = animelist.toDataFrame()
completedList

id                                              title  score  \
0     97636                        Akiba's Trip: The Animation     62   
1     20602                               Amagi Brilliant Park     74   
2     21077  Amagi Brilliant Park: Nonbirishiteiru Hima ga ...     70   
3      6547                                       Angel Beats!     79   
4     20755                                 Ansatsu Kyoushitsu     79   
..      ...                                                ...    ...   
97   104252                                  Maou-sama, Retry!     59   
98   107704                                    Kawaki wo Ameku     79   
99    99425                                            Promare     83   
100  107226                          Dumbbell Nan Kilo Moteru?     74   
101  112381                                      raison d'etre     64   

     popularity format  episode  duration       source  userScore  \
0         12475     TV       13        24   VIDEO_GAME       80.0   
1         42303     TV       13        24  LIGHT_NOVEL       70.0   
2          8614    OVA        1        24  LIGHT_NOVEL       70.0   
3         88258     TV       13        24     ORIGINAL       75.0   
4         72532     TV       22        23        MANGA       90.0   
..          ...    ...      ...       ...          ...        ...   
97        11116     TV       12        24  LIGHT_NOVEL       70.0   
98         1676  MUSIC        1         4        OTHER        0.0   
99         9545  MOVIE        1       115     ORIGINAL       95.0   
100       20176     TV       12        24        MANGA       80.0   
101         208  MUSIC        1         4     ORIGINAL        0.0   

              tag1                tag2                   tag3  genre1  \
0      Super Power       Otaku Culture                 Demons  Action   
1    Ensemble Cast               Magic       Male Protagonist  Comedy   
2    Ensemble Cast    Male Protagonist                   Work  Comedy   
3        Afterlife             Tragedy                 School  Action   
4        Assassins              School                Shounen  Action   
..             ...                 ...                    ...     ...   
97          Isekai           Anti-Hero       Male Protagonist  Action   
98         Musical  Female Protagonist  Primarily Female Cast   Music   
99    Firefighters              Robots                    CGI  Action   
100        Fitness         Educational              Athletics  Comedy   
101           None                None                   None   Music   

        genre2        genre3         genre4   genre5  
0        Ecchi  Supernatural         Comedy  Fantasy  
1      Romance       Fantasy           None     None  
2      Fantasy          None           None     None  
3       Comedy         Drama   Supernatural     None  
4       Comedy  Supernatural           None     None  
..         ...           ...            ...      ...  
97   Adventure       Fantasy           None     None  
98        None          None           None     None  
99       Mecha        Comedy         Sci-Fi     None  
100      Ecchi        Sports  Slice of Life     None  
101     Action          None           None     None  

[102 rows x 17 columns]

## Pré-traitement

Les données sont mis sous une forme plus adéquate pour le model (suppression des chaines de caractères) et une colonne like est ajoutée pour trier les anime en 2 class, ceux aimer par l'utilisateur (like = 1) et les autres (like = 0). On considère que tous anime avec un score égale ou supèrieur à 80 est aimé par l'utilisateur. De plus les colonnes titre, id et userScore sont supprimer car inutile pour l'apprentissage du model

In [5]:
df = animelist.toDataFrame(dummies = True)
df['like'] = 0
df.loc[df.userScore >= 80, 'like'] = 1
df = df.drop(['id', 'title', 'userScore'], axis=1)
df

score  popularity  episode  duration  tag_Super_Power  tag_Ensemble_Cast  \
0       62       12475       13        24                1                  0   
1       74       42303       13        24                0                  1   
2       70        8614        1        24                0                  1   
3       79       88258       13        24                0                  0   
4       79       72532       22        23                0                  0   
..     ...         ...      ...       ...              ...                ...   
97      59       11116       12        24                0                  0   
98      79        1676        1         4                0                  0   
99      83        9545        1       115                0                  0   
100     74       20176       12        24                0                  0   
101     64         208        1         4                0                  0   

     tag_Afterlife  tag_Assassins  tag_Cute_Girls_Doing_Cute_Things  \
0                0              0                                 0   
1                0              0                                 0   
2                0              0                                 0   
3                1              0                                 0   
4                0              1                                 0   
..             ...            ...                               ...   
97               0              0                                 0   
98               0              0                                 0   
99               0              0                                 0   
100              0              0                                 0   
101              0              0                                 0   

     tag_School  ...  format_OVA  format_SPECIAL  format_TV  \
0             0  ...           0               0          1   
1             0  ...           0               0          1   
2             0  ...           1               0          0   
3             1  ...           0               0          1   
4             1  ...           0               0          1   
..          ...  ...         ...             ...        ...   
97            0  ...           0               0          1   
98            0  ...           0               0          0   
99            0  ...           0               0          0   
100           0  ...           0               0          1   
101           0  ...           0               0          0   

     source_LIGHT_NOVEL  source_MANGA  source_ORIGINAL  source_OTHER  \
0                     0             0                0             0   
1                     1             0                0             0   
2                     1             0                0             0   
3                     0             0                1             0   
4                     0             1                0             0   
..                  ...           ...              ...           ...   
97                    1             0                0             0   
98                    0             0                0             1   
99                    0             0                1             0   
100                   0             1                0             0   
101                   0             0                1             0   

     source_VIDEO_GAME  source_VISUAL_NOVEL  like  
0                    1                    0     1  
1                    0                    0     0  
2                    0                    0     0  
3                    0                    0     0  
4                    0                    0     1  
..                 ...                  ...   ...  
97                   0                    0     0  
98                   0                    0     0  
99                   0                    0     1  
100                  0               

## Entrainement du model

Les données sont découpées en un jeu d'apprentissage (80% des données) et un jeu de test pour verifier le bonne apprentissage (20% des données). On entraine donc le model puis on le test jusqu'a avoir un niveau de prédiction supèrieur à 70% de réussite

In [6]:
# Separation x et y
y = df.like
x = df.drop('like', axis=1)
# Tant que la precision n'est pas suffisante
accuracy = 0
ite = 1
while accuracy < ACCURACYMIN:
    # Creation jeu d'apprentissage
    x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2)
    # Apprentissage du model
    model.fit(x_train, y_train)
    # Test du model
    y_predict = model.predict(x_test)
    elt, error, accuracy = valid_data(y_predict, y_test)
    # Affichage resultat apprentissage du model sur cette iteration
    print('Iteration', ite, ':', elt, 'elements,', error, 'erreur(s),', round(accuracy, 2), '% de precision')
    ite += 1
    # Si trop d'iteration on coupe
    if ITERATIONMAX != -1 and ite > ITERATIONMAX:
        raise Exception('Imposible to reach ' + str(ACCURACYMIN) + '% of accuracy')

Iteration 1 : 21 elements, 8 erreur(s), 61.9 % de precision
Iteration 2 : 21 elements, 4 erreur(s), 80.95 % de precision


## Récupération des features importantes

On récupére les features importantes pour qu'un anime plaise à l'utilisateur d'après le modèle

In [7]:
# Recuperation de la liste des features et de leur score associé par le model
feature_list = list(x.columns)
importances = list(model.feature_importances_)
feature_importances = [(feature, round(importance, 2)) for feature, importance in zip(feature_list, importances)]
# Transformation en DataFrame et on ne garde que les features avec un score supèrieur à 0.02
fi = pd.DataFrame(feature_importances, columns=['feature', 'score'])
fi = fi[fi.score >= 0.02]
fi

feature  score
0                     score   0.12
1                popularity   0.11
2                   episode   0.05
3                  duration   0.04
18                tag_Magic   0.02
22          tag_Video_Games   0.02
36   tag_Female_Protagonist   0.02
49     tag_Male_Protagonist   0.02
92             genre_Action   0.02
93             genre_Comedy   0.02
94      genre_Slice_of_Life   0.02
96       genre_Supernatural   0.02
99          genre_Adventure   0.02
107     genre_Psychological   0.02
117      source_LIGHT_NOVEL   0.02
118            source_MANGA   0.02

On interprete cette liste de features et on extrait les infos interessantes pour pouvoir requeter l'API après et récupèrer das anime susceptible de plaire à l'utilisateur

In [8]:
numerical = ['score', 'popularity', 'episode', 'duration']

# Extraction des features de type numerique
scoreMin = -1
popularityMin = -1
nbEpisodeMin = -1
nbEpisodeMax = -1
durationMin = -1
durationMax = -1
if 'score' in fi.feature.values:
    scoreMin = x.score.mean()
if 'popularity' in fi.feature.values:
    popularityMin = x.popularity.mean()
if 'episode' in fi.feature.values:
    mean = x.episode.mean()
    nbEpisodeMin = mean - 5
    nbEpisodeMax = mean + 5
if 'duration' in fi.feature.values:
    mean = x.duration.mean()
    durationMin = mean - 10
    durationMax = mean + 10

# Extraction des feature de type string
formatIn = []
sourceIn = []
genreIn = []
tagIn = []
for tpl in fi.itertuples():
    # Recuperation feature et passage feature numerique qui ont un traitement particulier
    feature = tpl[1]
    if feature in numerical:
        continue
    # Recuperation du nom du type de la feature et de sa valeur
    name = feature.split('_')
    if(len(name) > 2):
        feature = name[1] + '_' + name[2]
    else:
        feature = name[1]
    name = name[0]
    # Traitement
    if name == 'format':
        formatIn.append(feature)
    elif name == 'source':
        sourceIn.append(feature)
    elif name == 'genre':
        genreIn.append(feature)
    elif name == 'tag':
        tagIn.append(feature)
    else:
        raise ValueError("Unknown feature: " + name)

## Récupèration d'anime en fonction des features importantes

On requete l'api pour récupèrer des animes qui correspondent à nos features, puis ont les verifie les features qui ne peuvent pas être inclus dans la requete à l'api

In [9]:
# Creation de la query
query = make_query(score=scoreMin, popularity=popularityMin, source=sourceIn, formatType=formatIn)
# Creation variable pour receptionner les recommendations
col = x.columns.values
col = np.append(['id', 'title'], col)
finalList = pd.DataFrame(columns = col)
# On parcours plusieurs page 
for searchList in anilist.iterateAnimeListFetch(query, NBITERATION, NBANIME):
    # Si il n'y a plus de données
    if len(searchList.data) < 1:
        break
    # Transformation en DataFrame utilisable
    searchList = identical_features(x, searchList.toDataFrame(dummies = True), ['id', 'title'])
    # Verification des features nom presentes dans la requete
    valid = []
    for row in searchList.iterrows():
        isValid = False
        row = pd.Series(row[1])
        for genre in genreIn:
            if ('genre_' + genre) in row.index:
                isValid = True
                break
        if not isValid:
            for tag in tagIn:
                if ('tag_' + genre) in row.index:
                    isValid = True
                    break
        if isValid:
            valid.append(row)
    # Ajoute si tous est ok
    if len(valid) > 0:
        finalList = finalList.append(pd.DataFrame(valid), sort=False)

# Met en forme la liste final et l'affiche
finalList = identical_features(x, finalList.fillna(0), ['id', 'title'])
finalList

id                                              title  score  \
0     245                              Great Teacher Onizuka     84   
1   97922                                         Inuyashiki     73   
2   10162                                         Usagi Drop     83   
3   17549                                     Non Non Biyori     78   
4   14967                  Boku wa Tomodachi ga Sukunai Next     72   
..    ...                                                ...    ...   
45  14741                     Chuunibyou demo Koi ga Shitai!     76   
46  20920  Dungeon ni Deai wo Motomeru no wa Machigatteir...     74   
47   6746                                         Durarara!!     80   
48  10087                                          Fate/Zero     83   
49  20623                         Kiseijuu: Sei no Kakuritsu     82   

    popularity  episode  duration  tag_Super_Power  tag_Ensemble_Cast  \
0        31604     43.0        25                0                  0   
1        31631     11.0        23                0                  0   
2        31883     11.0        22                0                  0   
3        31976     12.0        24                0                  0   
4        31992     12.0        24                0                  0   
..         ...      ...       ...              ...                ...   
45       67649     12.0        24                0                  0   
46       68372     13.0        24                0                  0   
47       68550     24.0        24                0                  1   
48       70510     13.0        26                0                  1   
49       71072     24.0        24                0                  0   

    tag_Afterlife  tag_Assassins  ...  format_ONA  format_OVA  format_SPECIAL  \
0               0              0  ...           0           0               0   
1               0              0  ...           0           0               0   
2               0              0  ...           0           0               0   
3               0              0  ...           0           0               0   
4               0              0  ...           0           0               0   
..            ...            ...  ...         ...         ...             ...   
45              0              0  ...           0           0               0   
46              0              0  ...           0           0               0   
47              0              0  ...           0           0               0   
48              0              0  ...           0           0               0   
49              0              0  ...           0           0               0   

    format_TV  source_LIGHT_NOVEL  source_MANGA  source_ORIGINAL  \
0           1                   0             1                0   
1           1                   0             1                0   
2           1                   0             1                0   
3           1                   0             1                0   
4           1                   1             0                0   
..        ...                 ...           ...              ...   
45          1                   1             0                0   
46          1                   1             0                0   
47          1                   1             0                0   
48          1                   1             0                0   
49          1                   0             1                0   

    source_OTHER  source_VIDEO_GAME  source_VISUAL_NOVEL  
0              0                  0                    0  
1              0                  0                    0  
2              0                  0                    0  
3              0                  0                    0  
4              0                  0                    0  
..           ...                ...                  ...  
45             0                  0                    0  
46             

## Interrogation du model

On interroge le model pour savoir si les animes récupérés plairont ou non à l'utiliateur

In [10]:
# Liste des recommendations
recommendation = []
#On parcours chaque entrées de la liste fina
for row in finalList.iterrows():
    row = pd.Series(row[1])
    # Récupéréation id et titre puis suppr (elles sot inutiles au model)
    info = {'id': row.id, 'title': row.title}
    row = row.drop(['id', 'title'])
    # Prediction
    if model.predict([row])[0] == 1:
        recommendation.append(info)

# Transformation en DataFrame et suppression doublon
recommendation = pd.DataFrame(recommendation)
recommendation = recommendation.drop_duplicates()
recommendation

id                                              title
0    20652                                  Durarara!!x2 Shou
1     8425                                             Gosick
2    20593                                     Hanamonogatari
3     7674                                           Bakuman.
4    99726                                  Net-juu no Susume
..     ...                                                ...
97   20832                                           Overlord
98   14813  Yahari Ore no Seishun Love Comedy wa Machigatt...
99   20920  Dungeon ni Deai wo Motomeru no wa Machigatteir...
100   6746                                         Durarara!!
101  10087                                          Fate/Zero

[82 rows x 2 columns]

## Affichage resultat

On supprime tous les anime déjà vue par l'utilisateur et on affiche la liste 

In [11]:
# Récupèration uniquement des anime nom present dans la liste
result = []
for row in recommendation.iterrows():
    row = pd.Series(row[1])
    if completedList[completedList.id == row.id].empty:
        result.append(row.title)

# Affichage
result.sort()
print(len(result), 'recommendation(s)')
for anime in result:
    print('  -', anime)

69 recommendation(s)
  - Akatsuki no Yona
  - Akira
  - Baccano!
  - Bakuman.
  - Black Lagoon
  - Bleach
  - Dororo
  - Dr. STONE
  - Dragon Ball
  - Dragon Ball Z
  - Dungeon ni Deai wo Motomeru no wa Machigatteiru Darou ka
  - Dungeon ni Deai wo Motomeru no wa Machigatteiru Darou ka II
  - Durarara!!
  - Durarara!!x2 Shou
  - Enen no Shouboutai
  - Fairy Tail
  - Gintama
  - Gosick
  - Hagane no Renkinjutsushi
  - Hai to Gensou no Grimgar
  - Haikyuu!!
  - Haikyuu!! 2
  - Haikyuu!!: Karasuno Koukou VS Shiratorizawa Gakuen Koukou
  - Hanamonogatari
  - Hataraku Saibou
  - Hotarubi no Mori e
  - JoJo no Kimyou na Bouken
  - JoJo no Kimyou na Bouken: Diamond wa Kudakenai
  - JoJo no Kimyou na Bouken: Stardust Crusaders
  - JoJo no Kimyou na Bouken: Stardust Crusaders - Egypt-hen
  - Kaichou wa Maid-sama!
  - Katanagatari
  - Kekkai Sensen
  - Kimetsu no Yaiba
  - Kokoro Connect
  - Kono Subarashii Sekai ni Shukufuku wo! 2
  - Koukaku Kidoutai
  - Kuroko no Basket
  - Kyoukai no Kanata
